In [ ]:
from google import colab
colab.drive.mount("/content/drive")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import numpy as np
import pandas as pd

import torch
import torch.nn as nn
import torch.nn.functional as F

import warnings

warnings.filterwarnings(action='ignore')

In [ ]:
job_paths = '/content/drive/MyDrive/JobCare_data/'

train = pd.read_csv(job_paths + 'train.csv', low_memory=False).dropna(axis = 0)
test = pd.read_csv(job_paths + 'test.csv', low_memory=False).dropna(axis = 0)

In [ ]:
train = train.rename(columns={'id':'userId'})
test = test.rename(columns={'id':'userId'})

In [ ]:
train

userId  d_l_match_yn  ...     contents_open_dt  target
0            0          True  ...  2020-01-17 12:09:36       1
1            1         False  ...  2020-06-18 17:48:52       0
2            2         False  ...  2020-07-08 20:00:10       0
3            3         False  ...  2020-01-13 18:09:34       0
4            4          True  ...  2020-03-09 20:39:22       0
...        ...           ...  ...                  ...     ...
501946  501946         False  ...  2020-03-13 12:55:52       1
501947  501947          True  ...  2020-01-20 11:51:51       1
501948  501948          True  ...  2020-08-05 17:27:24       1
501949  501949          True  ...  2020-06-15 09:23:21       1
501950  501950          True  ...  2020-05-25 14:34:48       1

[501951 rows x 35 columns]

In [ ]:
test

userId  d_l_match_yn  ...  contents_rn     contents_open_dt
0           0          True  ...       236865  2020-12-01 02:24:18
1           1         False  ...       236572  2020-12-17 05:42:53
2           2          True  ...       704612  2020-12-10 23:33:41
3           3          True  ...       704652  2020-12-03 19:44:55
4           4          True  ...       704413  2020-12-11 21:24:34
...       ...           ...  ...          ...                  ...
46399   46399          True  ...       726084  2020-12-17 01:06:26
46400   46400          True  ...       156948  2020-12-29 21:57:25
46401   46401          True  ...       175069  2020-12-10 19:09:09
46402   46402          True  ...       174849  2020-12-07 14:04:34
46403   46403          True  ...       173406  2020-12-22 16:43:39

[46404 rows x 34 columns]

In [ ]:
COLUMNS = [
    "d_l_match_yn", "d_m_match_yn", "d_s_match_yn", "h_l_match_yn", "h_m_match_yn", 
    "h_s_match_yn", "person_attribute_a", "person_attribute_a_1", "person_attribute_b", "person_prefer_c", "person_prefer_d_1", "person_prefer_d_2",
    "person_prefer_d_3", "person_prefer_e", "person_prefer_h_1", "person_prefer_h_2", "person_prefer_h_3",
    "contents_attribute_i",	"contents_attribute_a",	"contents_attribute_j_1",	"contents_attribute_j", "contents_attribute_c",	"contents_attribute_k",
    "contents_attribute_l",	"contents_attribute_d",	"contents_attribute_m",	"contents_attribute_e",	"contents_attribute_h",	"person_rn",	"contents_rn",
]

CATEGORICAL_COLUMNS = [
    "d_l_match_yn", "d_m_match_yn", "d_s_match_yn", "h_l_match_yn", "h_m_match_yn", 
    "h_s_match_yn"
]

CONTINUOUS_COLUMNS = [
    "person_attribute_a", "person_attribute_a_1", "person_attribute_b", "person_prefer_c", "person_prefer_d_1", "person_prefer_d_2",
    "person_prefer_d_3", "person_prefer_e", "person_prefer_h_1", "person_prefer_h_2", "person_prefer_h_3",
    "contents_attribute_i",	"contents_attribute_a",	"contents_attribute_j_1",	"contents_attribute_j", "contents_attribute_c",	"contents_attribute_k",
    "contents_attribute_l",	"contents_attribute_d",	"contents_attribute_m",	"contents_attribute_e",	"contents_attribute_h",	"person_rn",	"contents_rn",
]

In [ ]:
from sklearn.preprocessing import LabelEncoder
for c in CATEGORICAL_COLUMNS:
    le = LabelEncoder()
    train[c] = le.fit_transform(train[c])

train

userId  d_l_match_yn  ...     contents_open_dt  target
0            0             1  ...  2020-01-17 12:09:36       1
1            1             0  ...  2020-06-18 17:48:52       0
2            2             0  ...  2020-07-08 20:00:10       0
3            3             0  ...  2020-01-13 18:09:34       0
4            4             1  ...  2020-03-09 20:39:22       0
...        ...           ...  ...                  ...     ...
501946  501946             0  ...  2020-03-13 12:55:52       1
501947  501947             1  ...  2020-01-20 11:51:51       1
501948  501948             1  ...  2020-08-05 17:27:24       1
501949  501949             1  ...  2020-06-15 09:23:21       1
501950  501950             1  ...  2020-05-25 14:34:48       1

[501951 rows x 35 columns]

In [ ]:
from sklearn.preprocessing import LabelEncoder
for c in CATEGORICAL_COLUMNS:
    le = LabelEncoder()
    test[c] = le.fit_transform(test[c])

test

userId  d_l_match_yn  ...  contents_rn     contents_open_dt
0           0             1  ...       236865  2020-12-01 02:24:18
1           1             0  ...       236572  2020-12-17 05:42:53
2           2             1  ...       704612  2020-12-10 23:33:41
3           3             1  ...       704652  2020-12-03 19:44:55
4           4             1  ...       704413  2020-12-11 21:24:34
...       ...           ...  ...          ...                  ...
46399   46399             1  ...       726084  2020-12-17 01:06:26
46400   46400             1  ...       156948  2020-12-29 21:57:25
46401   46401             1  ...       175069  2020-12-10 19:09:09
46402   46402             1  ...       174849  2020-12-07 14:04:34
46403   46403             1  ...       173406  2020-12-22 16:43:39

[46404 rows x 34 columns]

In [ ]:
# df = pd.concat([train, test])
# df

In [ ]:
X = train[COLUMNS]
y = train['target']

In [ ]:
X

d_l_match_yn  d_m_match_yn  ...  person_rn  contents_rn
0                  1             1  ...     618822       354805
1                  0             0  ...     571659       346213
2                  0             0  ...     399816       206408
3                  0             0  ...     827967       572323
4                  1             1  ...     831614       573899
...              ...           ...  ...        ...          ...
501946             0             0  ...     503156       285850
501947             1             1  ...     676255       456996
501948             1             1  ...     484528       293258
501949             1             0  ...     456330       273797
501950             1             1  ...     235596       176650

[501951 rows x 30 columns]

In [ ]:
y.head()

0    1
1    0
2    0
3    0
4    0
Name: target, dtype: int64

In [ ]:
X = X.values
y = y.values

In [ ]:
BATCH_SIZE = 128
EPOCHS = 100
num_classes = train['target'].nunique()

In [ ]:
# 환경설정
if torch.cuda.is_available():
  DEVICE = torch.device('cuda')
else:
  DEVICE = torch.device('cpu')
print(DEVICE)

cuda


In [ ]:
from torch.utils.data import Dataset
from torch.utils.data import DataLoader

class CustomDataset(Dataset):

  # 데이터 정의
  def __init__(self, x_data, y_data = None):
    self.x_data = (x_data - x_data.min(axis = 0)) / (x_data.max(axis = 0) - x_data.min(axis = 0))
    self.y_data = y_data

  # 이 데이터 셋의 총 데이터 수
  def __len__(self):
    return len(self.x_data)

  # 어떠한 idx를 받았을 때 그에 맞는 데이터를 반환
  def __getitem__(self, idx):
    if self.y_data is None:
      x = torch.FloatTensor(self.x_data[idx])
      return x
    else:
      x = torch.FloatTensor(self.x_data[idx])
      y = torch.LongTensor(self.y_data.reshape(-1,1)[idx])[0]
      return x, y

In [ ]:
# 추천시스템의 DNN은 기존 DNN의 성능 향상을 위한 테크닉이 적용되지 않는 다는 것을 알 수 있으며 
# 추천시스템의 DNN은 기존의 신경망들과 다른 방식으로 구성하는 것이 더 좋아보임  

class MLP(nn.Module):
  def __init__(self, num_classes):
    super(MLP, self).__init__()
    self.linear1 = nn.Sequential(
        nn.Linear(30, 512),
        # nn.BatchNorm1d(512), # 제거하는 것이 더 높은 성능을 보임
        nn.ReLU()
    )
    self.linear2 = nn.Sequential(
        nn.Linear(512, 256),
        # nn.BatchNorm1d(256),
        nn.ReLU()
    )
    self.linear3 = nn.Sequential(
        nn.Linear(256, 128),
        # nn.BatchNorm1d(128),
        nn.ReLU()
    )
    self.linear4 = nn.Sequential(
        nn.Linear(128, num_classes)
    )

  def forward(self, x):
    x = self.linear1(x)
    x = self.linear2(x)
    x = self.linear3(x)
    x = self.linear4(x)
    return x

In [ ]:
def weiht_init(model):
  if isinstance(model, nn.Linear):
    torch.nn.init.kaiming_uniform_(model.weight.data)

In [ ]:
model = MLP(num_classes).to(DEVICE)
model.apply(weiht_init)
optimizer = torch.optim.Adam(model.parameters(), lr = 2e-5)
criterion = nn.CrossEntropyLoss()

print(model)

MLP(
  (linear1): Sequential(
    (0): Linear(in_features=30, out_features=512, bias=True)
    (1): ReLU()
  )
  (linear2): Sequential(
    (0): Linear(in_features=512, out_features=256, bias=True)
    (1): ReLU()
  )
  (linear3): Sequential(
    (0): Linear(in_features=256, out_features=128, bias=True)
    (1): ReLU()
  )
  (linear4): Sequential(
    (0): Linear(in_features=128, out_features=2, bias=True)
  )
)


In [ ]:
def train(model, train_loader):
  model.train()
  train_loss = 0
  correct = 0

  for X_train, y_train in train_loader:
    X_train = X_train.to(DEVICE)
    y_train = y_train.to(DEVICE)
    optimizer.zero_grad()
    output = model(X_train)
    loss = criterion(output, y_train)
    loss.backward()
    optimizer.step()

    train_loss += loss.item()
    prediction = output.max(1, keepdim = True)[1]
    correct += prediction.eq(y_train.view_as(prediction)).sum().item()
      
  train_loss /= len(train_loader)
  train_accuracy = 100. * correct / len(train_loader.dataset)
  return train_loss, train_accuracy

In [ ]:
def evaluate(model, train_loader):
  model.eval()
  result = []
  correct = 0

  with torch.no_grad():
    for X_train, y_train in train_loader:
      X_train = X_train.to(DEVICE)
      y_train = y_train.to(DEVICE)
      output= model(X_train)
      result.append(F.softmax(output).cpu().numpy())

      prediction = output.max(1, keepdim = True)[1]
      correct += prediction.eq(y_train.view_as(prediction)).sum().item()

  train_accuracy = 100. * correct / len(train_loader.dataset)
  #result = np.concatenate(result)

  return result, train_accuracy

In [ ]:
train_dataset = CustomDataset(X, y)

train_loader = DataLoader(
  train_dataset,
  batch_size = BATCH_SIZE,
  shuffle = False,
  drop_last = False,
  )

for epoch in range(1, EPOCHS + 1):
  train_loss, train_accuracy = train(model, train_loader)
  print(f"\n[EPOCH: {epoch}], \tTrain Loss: {train_loss:.4f}, \tTrain Accuracy: {train_accuracy:.2f} %")


[EPOCH: 1], 	Train Loss: 0.5185, 	Train Accuracy: 70.34 %

[EPOCH: 2], 	Train Loss: 0.5263, 	Train Accuracy: 70.63 %

[EPOCH: 3], 	Train Loss: 0.5243, 	Train Accuracy: 70.76 %

[EPOCH: 4], 	Train Loss: 0.5237, 	Train Accuracy: 70.84 %

[EPOCH: 5], 	Train Loss: 0.5223, 	Train Accuracy: 70.92 %

[EPOCH: 6], 	Train Loss: 0.5215, 	Train Accuracy: 71.00 %

[EPOCH: 7], 	Train Loss: 0.5207, 	Train Accuracy: 71.06 %

[EPOCH: 8], 	Train Loss: 0.5200, 	Train Accuracy: 71.11 %

[EPOCH: 9], 	Train Loss: 0.5194, 	Train Accuracy: 71.15 %

[EPOCH: 10], 	Train Loss: 0.5188, 	Train Accuracy: 71.18 %

[EPOCH: 11], 	Train Loss: 0.5182, 	Train Accuracy: 71.22 %

[EPOCH: 12], 	Train Loss: 0.5177, 	Train Accuracy: 71.27 %

[EPOCH: 13], 	Train Loss: 0.5172, 	Train Accuracy: 71.30 %

[EPOCH: 14], 	Train Loss: 0.5167, 	Train Accuracy: 71.32 %

[EPOCH: 15], 	Train Loss: 0.5163, 	Train Accuracy: 71.37 %

[EPOCH: 16], 	Train Loss: 0.5159, 	Train Accuracy: 71.38 %

[EPOCH: 17], 	Train Loss: 0.5155, 	Train Accurac

In [ ]:
result, accuracy = evaluate(model, train_loader)
result

[array([[1.7360074e-04, 9.9982637e-01],
        [2.6049846e-04, 9.9973947e-01],
        [1.8039251e-03, 9.9819607e-01],
        [2.5038337e-04, 9.9974960e-01],
        [3.4057931e-04, 9.9965942e-01],
        [5.6404807e-04, 9.9943596e-01],
        [7.0016208e-04, 9.9929976e-01],
        [2.9555729e-04, 9.9970442e-01],
        [3.1655250e-04, 9.9968350e-01],
        [6.6328753e-04, 9.9933666e-01],
        [5.2297732e-05, 9.9994767e-01],
        [1.9254404e-03, 9.9807453e-01],
        [2.9502856e-04, 9.9970490e-01],
        [5.3446204e-04, 9.9946553e-01],
        [1.0741726e-03, 9.9892575e-01],
        [1.4309261e-04, 9.9985683e-01],
        [1.5781997e-03, 9.9842179e-01],
        [1.5231132e-04, 9.9984765e-01],
        [2.0219712e-04, 9.9979788e-01],
        [2.3143622e-03, 9.9768567e-01],
        [3.2957346e-04, 9.9967039e-01],
        [3.5431632e-03, 9.9645680e-01],
        [4.5013279e-03, 9.9549860e-01],
        [3.8901339e-03, 9.9610990e-01],
        [3.7595685e-04, 9.9962401e-01],


In [ ]:
print(f"Accuracy: {accuracy:.2f} %")

Accuracy: 49.97 %


In [ ]:
accuracy

49.97479833688946

In [ ]:
y

array([1, 0, 0, ..., 1, 1, 1])

In [ ]:
result = pd.DataFrame(result)

In [ ]:
result

0
0     [[0.00017360074, 0.9998264], [0.00026049846, 0...
1     [[0.00024995455, 0.9997501], [0.0010007628, 0....
2     [[0.00075692974, 0.99924314], [0.0004282893, 0...
3     [[0.00025243283, 0.9997476], [0.00088479347, 0...
4     [[0.00049680413, 0.99950314], [0.0004081694, 0...
...                                                 ...
3917  [[0.00025910046, 0.9997409], [0.0004912637, 0....
3918  [[0.0024690714, 0.997531], [0.00056047016, 0.9...
3919  [[6.412155e-05, 0.99993587], [0.00046024888, 0...
3920  [[0.00011789975, 0.9998821], [6.54154e-05, 0.9...
3921  [[0.0005302166, 0.9994698], [0.00011106332, 0....

[3922 rows x 1 columns]